In [1]:
import numpy as np
import numpy.linalg as LA
import scipy

In [2]:
effort_counter = {
    'function_eval':0,
    'derivative_eval':0,
    'hessian_eval':0
}


In [3]:
def compute_gradient(gradient_f,values):
    grad = []
    for derivative in gradient_f:
        gradient = derivative(*values)
        grad.append(gradient)
    return np.array(grad)

def compute_hessian(hessian_matrix,values):
    effort_counter['function_eval'] += 1
    hessian = []
    for row in hessian_matrix:
        row_val = []
        for element in row:
            row_value = element(*values)
            row_val.append(row_value)
        hessian.append(row_val)
    return np.array(hessian)
        

In [4]:
def descent_direction(gradient_f,values):
    grad = compute_gradient(gradient_f,values)
    descent_direction =  -(LA.norm(grad))**2
    return descent_direction

In [5]:
def armijo_step_algorithm(function,gradient,negative_grad,values,delta):
    step_size = 1
    descent = descent_direction(gradient,values)
    while function(*(values+step_size*negative_grad)) <= function(*values)+step_size*delta*descent:
        step_size *= 2
    
    while function(*(values+step_size*negative_grad)) > function(*values)+step_size*delta*descent:
        step_size /= 2
    return step_size   

In [6]:
def set_gradient_direction(function,gradient,hessian,values,direction_type,HK):
    dk = []
    grad = compute_gradient(gradient,values)
    if direction_type == 'newton':
        hess = compute_hessian(hessian,values)
        if check_gradient_relatedness(hess):
            dk = - np.dot(grad,LA.inv(hess))
            print('used newton')
        else:
            dk = -grad
            
    elif direction_type == 'quasi_newton':
        if is_gradient_related(HK):
            dk = -np.dot(HK,grad)
            print('used quasi')
        else:
            dk = - grad
            print('used grad')
    else:
        dk = - grad
    return dk

In [7]:
def is_gradient_related(matrix):
    eigen_values = LA.eigvalsh(matrix)
    if eigen_values[0]/eigen_values[len(eigen_values)-1] > 0:
        return True
    else:
        return False

In [ ]:
def inverse_update_BFGS(Hk1,Hk,function,gradient,xk1,xk):
    yk = compute_gradient(gradient,xk1) - compute_gradient(gradient,xk)
    sk = xk1-xk
    
    Hk1 = LA.inv(Hk1)
    Hk = LA.inv(Hk)
    
    common_denominator = np.outer(yk.T,sk)
    term1 = (np.outer((sk-np.dot(Hk,yk)),sk.T) + np.outer(sk, (sk-np.dot(Hk,yk)).T)) / common_denominator
    term2 = np.dot(np.outer((sk-np.dot(Hk1,yk)).T,yk),np.outer(sk,sk.T))/common_denominator**2

    Uk = term1 - term2

    Hk1 = Hk+ Uk
    Hk1 = Hk + Uk
    return Hk1

In [9]:
function = lambda x,y : 100*(y-x*x)**2 + (1-x)**2
dfx = lambda x,y: -400*x*(y-x*x) + 2*x - 2
dfy = lambda x,y: 200*(y-x*x)

dxdx = lambda x,y: (-400*(y-3*x**2)) + 2
dxdy = lambda x,y: -400*x
dydx = lambda x,y: -400*x
dydy = lambda x,y: 200

gradient = np.array([dfx,dfy])
hessian = np.array([np.array([dxdx,dydx]),np.array([dxdy,dydy])])



In [10]:
def general_descent(function,gradient_f,initial,direction_type,stopping_creiterion,max_iteration):
    xk = initial
    counter = 0
    xk1 = 0
    delta = 10**(-4)
    HK = None
    HK1 = None
    
    
    if direction_type == 'quasi_newton':
        HK = LA.inv(compute_hessian(hessian,initial))
        HK1 = HK
        print(HK)
    while LA.norm(compute_gradient(gradient,xk)) > stopping_creiterion:
        dk = set_gradient_direction(function,gradient,hessian,xk,direction_type,HK)
        step_size = armijo_step_algorithm(function,gradient,dk,xk,delta)
        xk1 = xk + step_size*dk
        if(direction_type == 'quasi_newton'):
            Hk1 = inverse_update_BFGS(HK1,HK,function,gradient,xk1,xk)
            Hk = Hk1
        xk = xk1
        print('xk1 at iterate: {}--->: {}'.format(counter,xk1))
        print('dk at iterate: {}--->: {}'.format(counter,dk))
        print('step_size at iterate: {}--->: {}'.format(counter,step_size))
        counter += 1
        if counter == max_iteration:
            break
    return xk1

In [14]:
minimizer = general_descent(function,gradient,np.array([3,2]),'quasi_newton',0.01,20000)
print('=================MINIMIZER===============',minimizer)
minimum = function(*minimizer)
print('=================MINIMMUM===============',minimum)

[[0.00035689 0.00214133]
 [0.00214133 0.01784797]]
used quasi
xk1 at iterate: 0--->: [2.99928622 5.49571734]
dk at iterate: 0--->: [-1.42755175e-03  6.99143469e+00]
step_size at iterate: 0--->: 0.5
used quasi
xk1 at iterate: 1--->: [2.99875102 7.24250637]
dk at iterate: 1--->: [-1.07040902e-03  3.49357806e+00]
step_size at iterate: 1--->: 0.5
used quasi
xk1 at iterate: 2--->: [2.9981937  8.11416311]
dk at iterate: 2--->: [-1.11463780e-03  1.74331348e+00]
step_size at iterate: 2--->: 0.5
used quasi
xk1 at iterate: 3--->: [2.99759338 8.54806238]
dk at iterate: 3--->: [-0.00120064  0.86779854]
step_size at iterate: 3--->: 0.5
used quasi
xk1 at iterate: 4--->: [2.99695562 8.76298766]
dk at iterate: 4--->: [-0.00127553  0.42985055]
step_size at iterate: 4--->: 0.5
used quasi
xk1 at iterate: 5--->: [2.99662304 8.81568103]
dk at iterate: 5--->: [-0.00133031  0.21077349]
step_size at iterate: 5--->: 0.25
used quasi
xk1 at iterate: 6--->: [2.99628653 8.85467911]
dk at iterate: 6--->: [-0.001346

dk at iterate: 101--->: [-0.00141174  0.00311346]
step_size at iterate: 101--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 102--->: [2.99331962 8.94837845]
dk at iterate: 102--->: [-0.00141174  0.00311346]
step_size at iterate: 102--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 103--->: [2.99331962 8.94837845]
dk at iterate: 103--->: [-0.00141174  0.00311346]
step_size at iterate: 103--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 104--->: [2.99331962 8.94837845]
dk at iterate: 104--->: [-0.00141174  0.00311346]
step_size at iterate: 104--->: 2.9103830456733704e-11
used quasi
xk1 at iterate: 105--->: [2.99331962 8.94837845]
dk at iterate: 105--->: [-0.00141174  0.00311346]
step_size at iterate: 105--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 106--->: [2.99331962 8.94837845]
dk at iterate: 106--->: [-0.00141174  0.00311346]
step_size at iterate: 106--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 107--->: [2.99331962 8.94837845]
dk at iterate: 107---

xk1 at iterate: 171--->: [2.99331962 8.94837845]
dk at iterate: 171--->: [-0.00141174  0.00311346]
step_size at iterate: 171--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 172--->: [2.99331962 8.94837845]
dk at iterate: 172--->: [-0.00141174  0.00311346]
step_size at iterate: 172--->: 2.9103830456733704e-11
used quasi
xk1 at iterate: 173--->: [2.99331962 8.94837845]
dk at iterate: 173--->: [-0.00141174  0.00311346]
step_size at iterate: 173--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 174--->: [2.99331962 8.94837845]
dk at iterate: 174--->: [-0.00141174  0.00311346]
step_size at iterate: 174--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 175--->: [2.99331962 8.94837845]
dk at iterate: 175--->: [-0.00141174  0.00311346]
step_size at iterate: 175--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 176--->: [2.99331962 8.94837845]
dk at iterate: 176--->: [-0.00141174  0.00311346]
step_size at iterate: 176--->: 2.9103830456733704e-11
used quasi
xk1 at iterate: 177-

dk at iterate: 230--->: [-0.00141174  0.00311345]
step_size at iterate: 230--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 231--->: [2.99331962 8.94837845]
dk at iterate: 231--->: [-0.00141174  0.00311345]
step_size at iterate: 231--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 232--->: [2.99331962 8.94837845]
dk at iterate: 232--->: [-0.00141174  0.00311345]
step_size at iterate: 232--->: 2.9103830456733704e-11
used quasi
xk1 at iterate: 233--->: [2.99331962 8.94837845]
dk at iterate: 233--->: [-0.00141174  0.00311345]
step_size at iterate: 233--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 234--->: [2.99331962 8.94837845]
dk at iterate: 234--->: [-0.00141174  0.00311345]
step_size at iterate: 234--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 235--->: [2.99331962 8.94837845]
dk at iterate: 235--->: [-0.00141174  0.00311345]
step_size at iterate: 235--->: 7.450580596923828e-09
used quasi
xk1 at iterate: 236--->: [2.99331962 8.94837845]
dk at iterate: 236---

step_size at iterate: 293--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 294--->: [2.99331961 8.94837845]
dk at iterate: 294--->: [-0.00141174  0.00311345]
step_size at iterate: 294--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 295--->: [2.99331961 8.94837845]
dk at iterate: 295--->: [-0.00141174  0.00311345]
step_size at iterate: 295--->: 2.9103830456733704e-11
used quasi
xk1 at iterate: 296--->: [2.99331961 8.94837845]
dk at iterate: 296--->: [-0.00141174  0.00311345]
step_size at iterate: 296--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 297--->: [2.99331961 8.94837845]
dk at iterate: 297--->: [-0.00141174  0.00311345]
step_size at iterate: 297--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 298--->: [2.99331961 8.94837845]
dk at iterate: 298--->: [-0.00141174  0.00311345]
step_size at iterate: 298--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 299--->: [2.99331961 8.94837845]
dk at iterate: 299--->: [-0.00141174  0.00311345]
step_size at iterate:

...

used quasi
xk1 at iterate: 19665--->: [2.99331948 8.94837875]
dk at iterate: 19665--->: [-0.00141174  0.00311234]
step_size at iterate: 19665--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19666--->: [2.99331948 8.94837875]
dk at iterate: 19666--->: [-0.00141174  0.00311234]
step_size at iterate: 19666--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19667--->: [2.99331948 8.94837875]
dk at iterate: 19667--->: [-0.00141174  0.00311234]
step_size at iterate: 19667--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19668--->: [2.99331948 8.94837875]
dk at iterate: 19668--->: [-0.00141174  0.00311234]
step_size at iterate: 19668--->: 9.313225746154785e-10
used quasi
xk1 at iterate: 19669--->: [2.99331948 8.94837875]
dk at iterate: 19669--->: [-0.00141174  0.00311234]
step_size at iterate: 19669--->: 7.450580596923828e-09
used quasi
xk1 at iterate: 19670--->: [2.99331948 8.94837875]
dk at iterate: 19670--->: [-0.00141174  0.00311234]
step_size at iterate: 19670--->: 9.313225

xk1 at iterate: 19723--->: [2.99331948 8.94837875]
dk at iterate: 19723--->: [-0.00141174  0.00311234]
step_size at iterate: 19723--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19724--->: [2.99331948 8.94837875]
dk at iterate: 19724--->: [-0.00141174  0.00311234]
step_size at iterate: 19724--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19725--->: [2.99331948 8.94837875]
dk at iterate: 19725--->: [-0.00141174  0.00311234]
step_size at iterate: 19725--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19726--->: [2.99331948 8.94837875]
dk at iterate: 19726--->: [-0.00141174  0.00311234]
step_size at iterate: 19726--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19727--->: [2.99331948 8.94837875]
dk at iterate: 19727--->: [-0.00141174  0.00311234]
step_size at iterate: 19727--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19728--->: [2.99331948 8.94837875]
dk at iterate: 19728--->: [-0.00141174  0.00311234]
step_size at iterate: 19728--->: 3.725290298461914e-

step_size at iterate: 19832--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19833--->: [2.99331948 8.94837875]
dk at iterate: 19833--->: [-0.00141174  0.00311234]
step_size at iterate: 19833--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19834--->: [2.99331948 8.94837875]
dk at iterate: 19834--->: [-0.00141174  0.00311234]
step_size at iterate: 19834--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19835--->: [2.99331948 8.94837875]
dk at iterate: 19835--->: [-0.00141174  0.00311234]
step_size at iterate: 19835--->: 9.313225746154785e-10
used quasi
xk1 at iterate: 19836--->: [2.99331948 8.94837875]
dk at iterate: 19836--->: [-0.00141174  0.00311234]
step_size at iterate: 19836--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19837--->: [2.99331948 8.94837875]
dk at iterate: 19837--->: [-0.00141174  0.00311234]
step_size at iterate: 19837--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19838--->: [2.99331948 8.94837875]
dk at iterate: 19838--->: [-0.00141174

dk at iterate: 19910--->: [-0.00141174  0.00311233]
step_size at iterate: 19910--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19911--->: [2.99331948 8.94837875]
dk at iterate: 19911--->: [-0.00141174  0.00311233]
step_size at iterate: 19911--->: 9.313225746154785e-10
used quasi
xk1 at iterate: 19912--->: [2.99331948 8.94837875]
dk at iterate: 19912--->: [-0.00141174  0.00311233]
step_size at iterate: 19912--->: 7.450580596923828e-09
used quasi
xk1 at iterate: 19913--->: [2.99331948 8.94837875]
dk at iterate: 19913--->: [-0.00141174  0.00311233]
step_size at iterate: 19913--->: 9.313225746154785e-10
used quasi
xk1 at iterate: 19914--->: [2.99331948 8.94837875]
dk at iterate: 19914--->: [-0.00141174  0.00311233]
step_size at iterate: 19914--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19915--->: [2.99331948 8.94837875]
dk at iterate: 19915--->: [-0.00141174  0.00311233]
step_size at iterate: 19915--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19916--->: [2.9933194

xk1 at iterate: 19960--->: [2.99331948 8.94837875]
dk at iterate: 19960--->: [-0.00141174  0.00311233]
step_size at iterate: 19960--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19961--->: [2.99331948 8.94837875]
dk at iterate: 19961--->: [-0.00141174  0.00311233]
step_size at iterate: 19961--->: 3.725290298461914e-09
used quasi
xk1 at iterate: 19962--->: [2.99331948 8.94837875]
dk at iterate: 19962--->: [-0.00141174  0.00311233]
step_size at iterate: 19962--->: 9.313225746154785e-10
used quasi
xk1 at iterate: 19963--->: [2.99331948 8.94837875]
dk at iterate: 19963--->: [-0.00141174  0.00311233]
step_size at iterate: 19963--->: 7.450580596923828e-09
used quasi
xk1 at iterate: 19964--->: [2.99331948 8.94837875]
dk at iterate: 19964--->: [-0.00141174  0.00311233]
step_size at iterate: 19964--->: 9.313225746154785e-10
used quasi
xk1 at iterate: 19965--->: [2.99331948 8.94837875]
dk at iterate: 19965--->: [-0.00141174  0.00311233]
step_size at iterate: 19965--->: 7.450580596923828e-

In [12]:
a = np.array([3,2])
b = np.array([2,2])
c = np.array([2,1])

print(np.dot(a,np.dot(b,c)))
print(np.dot(np.dot(a,b),c))


[18 12]
[20 10]
